# Business Problem

The following analysis solves the problem of finding similar areas in the city of Madrid (Spain) attending to similarity in the venues contained in each area of the city. 

This analysis will be useful for a real estate business that wants to advise potential customers which are the areas in Madrid  match better the customers preferences in terms of services, businesses or any other venue that it is possible to find in each of these areas. 

An example of why this is useful for the customer is the following: the customer likes a certain area, but the prices are too expensive. So the client asks the real estate which other areas are the best alternatives (i.e. the most similar). We will use this work to find the closest alternative areas for the given model provided by the client (his/her favorite, but expensive, area to live). 

# Location Data used to perform the analysis

Our first step will be to divide the city of Madrid in areas distributed across the whole territory. For that purpose, we will use all the Postal Codes that exist in the city. 

A complete list of the postal code can be found here:
http://distritopostal.es/madrid/madrid
    
There are 55 in total, which will be writeen directly in the program. 

Once we have the postal codes ready to be used, the Foursquare will be used to retrieve the following information:
- Coordinates of each postal code.
- Venues that are located on each postal code.
- The coordinates of each individual venue. 

We will use a radius of 1000 meters to retrieve the data around each postal code area. 

For **example**, we will get the information for the postal code **28003** in Madrid, which is near to the center. Later, we will retrieve the latitude and longitude associated to that postal code, and after that we will find which venues can be found in a radius of 1000 meters around the postal code location given by Foursquare. We will repeat the procedure for all the Postal Codes.

# Methodology used to find similarities among Postal Code areas

First, we will identifiy the top 10 most common venues for each postal code area. 

Secondly, we will group all the postal code areas in clusters attending to similarities in the venues present in those areas. 

We will use K-Means algorithm to make such groups. All the 55 Postal Codes will be reduced to 5 group (or clusters). 

Finally, we will show which areas are similar using the clasification given by K-Means: all areas included in the same cluster will be considered as similar. The customer will just find his/her favorite area, given by the postal code, in the same cluster as other areas. Those areas will be the customers alternatives to find similar neighborhoods for their future home.  

# Import Libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0          conda-forge
    geopy:           

## Postal Codes in Madrid into a Data Frame

In [2]:
postcode_list=np.dtype(object)  

postcode_list = ['28001','28002','28003','28004','28005','28006','28007','28008','28009','28010','28011','28012','28013','28014',
'28015','28016','28017','28018','28019','28020','28021','28022','28023','28024','28025','28026','28027',
'28028','28029','28030','28031','28032','28033','28034','28035','28036','28037','28038','28039','28040',
'28041','28042','28043','28044','28045','28046','28047','28048','28049','28050','28051','28052','28053',
'28054','28055','28000']

postcode_list = pd.DataFrame(postcode_list)

## Foursquare API Credentials

In [45]:
# The code was removed by Watson Studio for sharing.

## Get coordinates for each Postal Code and merge them in a single Data Frame

In [4]:
address_vector = postcode_list + ' España'

geolocator = Nominatim(user_agent="foursquare_agent")

lat_lng = []

for n in address_vector[0]:
    location = geolocator.geocode(n)
    latitude = location.latitude
    longitude = location.longitude
    lat_lng.append([
        latitude,
        longitude])

lat_lng = pd.DataFrame(lat_lng)

lat_lng.columns = ['postCode_lat','postCode_lng']
postcode_list.columns = ['postCode']

postcode_list['postCode_lat'] = lat_lng['postCode_lat']
postcode_list['postCode_lng'] = lat_lng['postCode_lng']

In [5]:
postcode_list.head()

postCode  postCode_lat  postCode_lng
0    28001     40.424066     -3.686055
1    28002     40.444363     -3.671973
2    28003     40.439374     -3.699367
3    28004     40.428463     -3.703477
4    28005     40.408363     -3.708580

## Taking a preliminary look at the distribution of all postal codes location over the territory in Madrid City

In [6]:
address = 'Madrid, MA'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Madrid are {}, {}.'.format(latitude, longitude))

# create map of Manhattan using latitude and longitude values
map_madrid = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(postcode_list['postCode_lat'], postcode_list['postCode_lng'], postcode_list['postCode']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_madrid)  
    
map_madrid

The geograpical coordinate of Madrid are 40.4167047, -3.7035825.


## Define functions to extract information abut the venues for each postal code

In [7]:
def getNearbyVenues(postCodes, latitudes, longitudes, radius=1000, LIMIT = 100):
    
    venues_list=[]
    for postCode, lat, lng in zip(postCodes, latitudes, longitudes):
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            postCode, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['postCode', 
                  'postCode Latitude', 
                  'postCode Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [8]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

## Get Venues in Madrid for each Postal Code


In [9]:
madrid_venues = getNearbyVenues(postCodes=postcode_list['postCode'],
                                   latitudes=postcode_list['postCode_lat'],
                                   longitudes=postcode_list['postCode_lng']
                                  )

## Mark each venue in the map for a general overview

In [10]:
# add markers to map
for lat, lng, label in zip(madrid_venues['Venue Latitude'], madrid_venues['Venue Longitude'], madrid_venues['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_madrid)  

# add markers to map
for lat, lng, label in zip(postcode_list['postCode_lat'], postcode_list['postCode_lng'], postcode_list['postCode']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=6,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_madrid)  
        
map_madrid

## Counting venues by category

In [11]:
madrid_venues.groupby('Venue Category').count()

postCode  postCode Latitude  \
Venue Category                                                          
Accessories Store                                3                  3   
Airport                                          1                  1   
Airport Terminal                                 3                  3   
American Restaurant                             13                 13   
Aquarium                                         1                  1   
Arcade                                           1                  1   
Arepa Restaurant                                 2                  2   
Argentinian Restaurant                          16                 16   
Art Gallery                                     22                 22   
Art Museum                                      16                 16   
Art Studio                                       1                  1   
Arts & Crafts Store                              1                  1   
Asian Restaurant                                33                 33   
Athletics & Sports                              13                 13   
Auto Workshop                                    2                  2   
BBQ Joint                                       13                 13   
Bakery                                          74                 74   
Bar                                            137                137   
Basketball Stadium                               1                  1   
Beach                                            1                  1   
Bed & Breakfast                                  2                  2   
Beer Bar                                        10                 10   
Beer Garden                                     17                 17   
Beer Store                                       6                  6   
Big Box Store                                    6                  6   
Bike Trail                                       1                  1   
Bistro                                          13                 13   
Boat or Ferry                                    1                  1   
Bookstore                                       32                 32   
Boutique                                        10                 10   
Bowling Alley                                    1                  1   
Boxing Gym                                       1                  1   
Brazilian Restaurant                             3                  3   
Breakfast Spot                                  31                 31   
Brewery                                         34                 34   
Bridge                                           1                  1   
Bubble Tea Shop                                  1                  1   
Building                                         2                  2   
Burger Joint                                    50                 50   
Burrito Place                                    7                  7   
Bus Station                                      1                  1   
Cafeteria                                        1                  1   
Café                                            92                 92   
Camera Store                                     2                  2   
Candy Store                                      4                  4   
Casino                                           3                  3   
Cheese Shop                                      2                  2   
Chinese Restaurant                              21                 21   
Chocolate Shop                                   2                  2   
Church                                           6                  6   
Circus                                           2                  2   
Clothing Store                                  28                 28   
Cocktail Bar                                    27                 27   
Coffee Shop                

In [12]:
print('There are {} uniques categories.'.format(len(madrid_venues['Venue Category'].unique())))

There are 268 uniques categories.


## Analyze Each Post Code area

In [13]:
# one hot encoding
madrid_onehot = pd.get_dummies(madrid_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
madrid_onehot['postCode'] = madrid_venues['postCode'] 

# move neighborhood column to the first column
fixed_columns = [madrid_onehot.columns[-1]] + list(madrid_onehot.columns[:-1])
madrid_onehot = madrid_onehot[fixed_columns]

madrid_onehot.head()

postCode  Accessories Store  Airport  Airport Terminal  American Restaurant  \
0    28001                  0        0                 0                    0   
1    28001                  0        0                 0                    0   
2    28001                  0        0                 0                    0   
3    28001                  0        0                 0                    0   
4    28001                  0        0                 0                    0   

   Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0         0       0                 0                       0            0   
1         0       0                 0                       0            0   
2         0       0                 0                       0            0   
3         0       0                 0                       0            0   
4         0       0                 0                       0            0   

   Art Museum  Art Studio  Arts & Crafts Store  Asian Restaurant  \
0           0           0                    0                 0   
1           0           0                    0                 0   
2           0           0                    0                 0   
3           0           0                    0                 0   
4           0           0                    0                 0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Bakery  Bar  \
0                   0              0          0       0    0   
1                   0              0          0       0    0   
2                   0              0          0       0    0   
3                   0              0          0       0    0   
4                   0              0          0       0    0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                   0      0                0         0            0   
1                   0      0                0         0            0   
2                   0      0                0         0            0   
3                   0      0                0         0            0   
4                   0      0                0         0            0   

   Beer Store  Big Box Store  Bike Trail  Bistro  Boat or Ferry  Bookstore  \
0           0              0           0       0              0          0   
1           0              0           0       0              0          0   
2           0              0           0       0              0          0   
3           0              0           0       0              0          0   
4           0              0           0       0              0          0   

   Boutique  Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  \
0         0              0           0                     0               0   
1         0              0           0                     0               0   
2         0              0           0                     0               0   
3         0              0           0                     0               0   
4         0              0           0                     0               0   

   Brewery  Bridge  Bubble Tea Shop  Building  Burger Joint  Burrito Place  \
0        0       0                0         0             0              0   
1        0       0                0         0             0              0   
2        0       0                0         0             0              0   
3        0       0                0         0             0              0   
4        0       0                0         0             0              0   

   Bus Station  Cafeteria  Café  Camera Store  Candy Store  Casino  \
0            0          0     0             0            0       0   
1            0          0     0             0            0       0   
2            0          0     0             0            0       0   
3            0          0     0             0            0       0   
4            0          0     0             0     

In [14]:
madrid_onehot.shape

(3479, 269)

### Group rows by postCode and by taking the mean of the frequency of occurrence of each category

In [15]:
madrid_grouped = madrid_onehot.groupby('postCode').mean().reset_index()

In [16]:
madrid_grouped.shape

(56, 269)

In [17]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

## Top 10 Venues by postal code

In [18]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['postCode']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
postCodes_venues_sorted = pd.DataFrame(columns=columns)
postCodes_venues_sorted['postCode'] = madrid_grouped['postCode']

for ind in np.arange(madrid_grouped.shape[0]):
    postCodes_venues_sorted.iloc[ind, 1:] = return_most_common_venues(madrid_grouped.iloc[ind, :], num_top_venues)

postCodes_venues_sorted.head()

postCode 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0    28000    Spanish Restaurant            Restaurant      Tapas Restaurant   
1    28001            Restaurant    Spanish Restaurant    Italian Restaurant   
2    28002    Spanish Restaurant            Restaurant                 Hotel   
3    28003    Spanish Restaurant      Tapas Restaurant            Restaurant   
4    28004            Restaurant      Tapas Restaurant                 Plaza   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                   Bar   Japanese Restaurant                  Café   
1              Boutique      Tapas Restaurant   Japanese Restaurant   
2      Tapas Restaurant           Supermarket      Theme Restaurant   
3                  Café   Japanese Restaurant                   Bar   
4             Bookstore                  Café                   Bar   

  7th Most Common Venue     8th Most Common Venue      9th Most Common Venue  \
0                 Plaza        Italian Restaurant                    Brewery   
1                 Hotel              Burger Joint                     Bakery   
2                  Café  Mediterranean Restaurant  Middle Eastern Restaurant   
3                 Plaza        Italian Restaurant               Burger Joint   
4    Spanish Restaurant                     Hotel             Ice Cream Shop   

  10th Most Common Venue  
0                  Hotel  
1         Clothing Store  
2       Sushi Restaurant  
3                 Bakery  
4            Coffee Shop

## Cluster Neighborhoods

In [19]:
# set number of clusters
kclusters = 5

madrid_grouped_clustering = madrid_grouped.drop('postCode', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(madrid_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 2, 2, 2, 2, 1, 2, 2], dtype=int32)

## Clusters Data Frame

In [20]:
# add clustering labels
postCodes_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

madrid_merged = postcode_list

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
madrid_merged = madrid_merged.join(postCodes_venues_sorted.set_index('postCode'), on='postCode')

madrid_merged.head() # check the last columns!

postCode  postCode_lat  postCode_lng  Cluster Labels 1st Most Common Venue  \
0    28001     40.424066     -3.686055               2            Restaurant   
1    28002     40.444363     -3.671973               2    Spanish Restaurant   
2    28003     40.439374     -3.699367               2    Spanish Restaurant   
3    28004     40.428463     -3.703477               2            Restaurant   
4    28005     40.408363     -3.708580               2      Tapas Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0    Spanish Restaurant    Italian Restaurant              Boutique   
1            Restaurant                 Hotel      Tapas Restaurant   
2      Tapas Restaurant            Restaurant                  Café   
3      Tapas Restaurant                 Plaza             Bookstore   
4    Spanish Restaurant                 Plaza                   Bar   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0      Tapas Restaurant   Japanese Restaurant                 Hotel   
1           Supermarket      Theme Restaurant                  Café   
2   Japanese Restaurant                   Bar                 Plaza   
3                  Café                   Bar    Spanish Restaurant   
4           Coffee Shop           Art Gallery                 Hotel   

      8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
0              Burger Joint                     Bakery         Clothing Store  
1  Mediterranean Restaurant  Middle Eastern Restaurant       Sushi Restaurant  
2        Italian Restaurant               Burger Joint                 Bakery  
3                     Hotel             Ice Cream Shop            Coffee Shop  
4               Pizza Place                 Restaurant                 Market

## Map Clusters

In [21]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(madrid_merged['postCode_lat'], madrid_merged['postCode_lng'], madrid_merged['postCode'], madrid_merged['Cluster Labels'].fillna(0).astype(int)):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine Clusters

#### Cluster 1

In [22]:
madrid_merged.loc[madrid_merged['Cluster Labels'] == 0, madrid_merged.columns[[0] + list(range(4, madrid_merged.shape[1]))]]

postCode 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
48    28049      Department Store                   Pub                 Diner   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
48                  Café            Food Court           Flea Market   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
48           Flower Shop                  Food     Food & Drink Shop   

   10th Most Common Venue  
48             Food Stand

#### Cluster 2

In [23]:
madrid_merged.loc[madrid_merged['Cluster Labels'] == 1, madrid_merged.columns[[0] + list(range(4, madrid_merged.shape[1]))]]

postCode 1st Most Common Venue     2nd Most Common Venue  \
6     28007    Spanish Restaurant                    Museum   
10    28011    Spanish Restaurant                      Park   
16    28017    Spanish Restaurant                       Bar   
17    28018           Pizza Place                      Park   
18    28019    Spanish Restaurant                       Bar   
20    28021        Sandwich Place                      Café   
22    28023         Deli / Bodega                      Café   
23    28024    Italian Restaurant                       Bar   
24    28025  Fast Food Restaurant          Tapas Restaurant   
25    28026    Spanish Restaurant             Grocery Store   
28    28029    Spanish Restaurant            Clothing Store   
30    28031            Restaurant             Metro Station   
31    28032               Exhibit        Spanish Restaurant   
32    28033                  Park        Spanish Restaurant   
34    28035      Tapas Restaurant        Spanish Restaurant   
35    28036                 Hotel                       Bar   
37    28038                   Bar               Pizza Place   
39    28040                  Park            Breakfast Spot   
40    28041    Spanish Restaurant               Pizza Place   
41    28042    Spanish Restaurant                     Hotel   
42    28043    Spanish Restaurant                       Bar   
43    28044           Supermarket        Spanish Restaurant   
44    28045            Restaurant        Spanish Restaurant   
46    28047           Pizza Place      Fast Food Restaurant   
49    28050    Spanish Restaurant                Restaurant   
50    28051      Sushi Restaurant               Pizza Place   
51    28052            Restaurant  Mediterranean Restaurant   
52    28053           Pizza Place                       Bar   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6                      Hotel                Bakery   Peruvian Restaurant   
10             Grocery Store           Beer Garden           Pizza Place   
16                    Bakery         Grocery Store            Restaurant   
17               Supermarket                   Bar      Tapas Restaurant   
18                      Park      Tapas Restaurant           Pizza Place   
20             Grocery Store                Bakery    Athletics & Sports   
22        Spanish Restaurant                   Gym                 Diner   
23               Pizza Place         Grocery Store                 Diner   
24             Grocery Store               Stadium        Breakfast Spot   
25                       Bar    Seafood Restaurant           Coffee Shop   
28      Fast Food Restaurant                  Park      Tapas Restaurant   
30                       Gym         Grocery Store    Spanish Restaurant   
31               Supermarket      Tapas Restaurant                  Park   
32                Food Truck         Grocery Store           Supermarket   
34               Pizza Place                 Diner                   Bar   
35      Gym / Fitness Center           Coffee Shop              Platform   
37        Spanish Restaurant         Grocery Store                  Café   
39                    Garden           Music Venue           Coffee Shop   
40               Supermarket                  Café      Tapas Restaurant   
41                 Hotel Bar                Bakery            Restaurant   
42        Italian Restaurant                  Park           Pizza Place   
43          Tapas Restaurant           Pizza Place                  Café   
44               Art Gallery      Tapas Restaurant                Garden   
46                      Park    Italian Restaurant         Grocery Store   
49  Mediterranean Restaurant    Italian Restaurant                 Hotel   
50              Cupcake Shop      Asian Restaurant           Supermarket   
51                       Gym         Train Station                  Park   
52             Grocery Store           Supermar

#### Cluster 3

In [24]:
madrid_merged.loc[madrid_merged['Cluster Labels'] == 2, madrid_merged.columns[[0] + list(range(4, madrid_merged.shape[1]))]]

postCode 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0     28001            Restaurant    Spanish Restaurant    Italian Restaurant   
1     28002    Spanish Restaurant            Restaurant                 Hotel   
2     28003    Spanish Restaurant      Tapas Restaurant            Restaurant   
3     28004            Restaurant      Tapas Restaurant                 Plaza   
4     28005      Tapas Restaurant    Spanish Restaurant                 Plaza   
5     28006    Spanish Restaurant            Restaurant      Tapas Restaurant   
7     28008                 Hotel    Spanish Restaurant      Tapas Restaurant   
8     28009    Spanish Restaurant            Restaurant      Tapas Restaurant   
9     28010      Tapas Restaurant    Spanish Restaurant                 Plaza   
11    28012                 Plaza            Restaurant                  Café   
12    28013                 Plaza                 Hotel                  Café   
13    28014            Restaurant                 Plaza                 Hotel   
14    28015      Tapas Restaurant    Spanish Restaurant           Coffee Shop   
15    28016            Restaurant    Spanish Restaurant   Japanese Restaurant   
19    28020    Spanish Restaurant                   Bar                 Hotel   
26    28027    Spanish Restaurant      Tapas Restaurant                   Bar   
27    28028    Spanish Restaurant    Seafood Restaurant            Restaurant   
33    28034            Restaurant           Coffee Shop    Spanish Restaurant   
36    28037            Restaurant    Spanish Restaurant                 Hotel   
38    28039    Spanish Restaurant                   Bar            Restaurant   
45    28046    Spanish Restaurant            Restaurant  Gym / Fitness Center   
47    28048    Spanish Restaurant            Restaurant                 Plaza   
53    28054    Spanish Restaurant                   Bar          Music School   
55    28000    Spanish Restaurant            Restaurant      Tapas Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0               Boutique      Tapas Restaurant   Japanese Restaurant   
1       Tapas Restaurant           Supermarket      Theme Restaurant   
2                   Café   Japanese Restaurant                   Bar   
3              Bookstore                  Café                   Bar   
4                    Bar           Coffee Shop           Art Gallery   
5            Coffee Shop                 Hotel              Boutique   
7                  Plaza                  Park          Cocktail Bar   
8     Italian Restaurant                Bakery        Ice Cream Shop   
9             Restaurant                   Bar    Italian Restaurant   
11           Coffee Shop                 Hotel    Spanish Restaurant   
12      Tapas Restaurant             Bookstore                Hostel   
13            Art Museum      Tapas Restaurant                  Café   
14                  Café        Ice Cream Shop                   Bar   
15                 Plaza             Gastropub    Seafood Restaurant   
19    Seafood Restaurant            Restaurant      Tapas Restaurant   
26           Supermarket            Restaurant         Grocery Store   
27     Indian Restaurant           Supermarket    Mexican Restaurant   
33                 Hotel                  Café      Tapas Restaurant   
36           Supermarket                  Café        Sandwich Place   
38      Tapas Restaurant                Bakery  Gym / Fitness Center   
45              Platform      Tapas Restaurant                   Bar   
47                Bakery   Government Building      Tapas Restaurant   
53            Restaurant  Gym / Fitness Center            Steakhouse   
55                   Bar   Japanese Restaurant                  Café   

       7th Most Common Venue     8th Most Common Venue  \
0                      Hotel              Burger Joint   
1                       Café  Mediterranean Restaurant   
2 

#### Cluster 4

In [25]:
madrid_merged.loc[madrid_merged['Cluster Labels'] == 3, madrid_merged.columns[[0] + list(range(4, madrid_merged.shape[1]))]]

postCode 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
54    28055            Restaurant      Airport Terminal                 Diner   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
54                  Park  Gym / Fitness Center      Asian Restaurant   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
54                   Zoo     Food & Drink Shop           Fish Market   

   10th Most Common Venue  
54            Flea Market

#### Cluster 5

In [26]:
madrid_merged.loc[madrid_merged['Cluster Labels'] == 4, madrid_merged.columns[[0] + list(range(4, madrid_merged.shape[1]))]]

postCode 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
21    28022           Sports Club                 Trail        Soccer Stadium   
29    28030                 Plaza                   Bar         Metro Station   

   4th Most Common Venue 5th Most Common Venue     6th Most Common Venue  \
21              Beer Bar                  Park  Mediterranean Restaurant   
29                  Café                  Park               Coffee Shop   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
21         Metro Station   Sporting Goods Shop                 Plaza   
29                Bakery          Concert Hall           Supermarket   

   10th Most Common Venue  
21                  Diner  
29       Sushi Restaurant

## Conclusion

We have classified all the Postal Codes in Madrid in 5 clusters according to their similarities in venues and services provided in those areas. We can now make an analysis to provide the customers with alternatives of possible areas that are as close ass possible to one favorite area chose by the customers. 

For example, if one customer desires to live in the area which has the Postal Code **28003** but it is too expensive, he/she could choose the most similar ones. In particular, **28003** is located in the **cluster 3**, which also has the following alternatives:

In [41]:
madrid_merged.loc[madrid_merged['Cluster Labels'] == 2, madrid_merged.columns[[0] + list(range(1, 1))]]

postCode
0     28001
1     28002
2     28003
3     28004
4     28005
5     28006
7     28008
8     28009
9     28010
11    28012
12    28013
13    28014
14    28015
15    28016
19    28020
26    28027
27    28028
33    28034
36    28037
38    28039
45    28046
47    28048
53    28054
55    28000